<a href="https://colab.research.google.com/github/omarmohamed101/cape/blob/main/CAPE_demo.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Demo for the CVPR 2020 paper "Learning to Dress 3D People in Generative Clothing"
    
### Note:
- Before running this notebook make sure that your runtime type is 'Python 3 with GPU acceleration'. Go to Edit > Notebook settings > Hardware Accelerator > Select "GPU".
- This demo will dress a minimally-clothed body with generated clothing. For the full demo (including reposing the dressed body), one would need the SMPL body model that needs to be separately downloaded. Please visit our [Github repository](https://github.com/QianliM/CAPE) for the instructions to run the full demo.  

### More Info:
- [Paper on arXiv](https://arxiv.org/abs/1907.13615)
- Also check out our [project page](https://cape.is.tue.mpg.de/) for the CAPE Dataset, a large scale 3D mesh dataset of clothed humans in motion.


### 0. Enable GPU environment for this demo
Go to Edit > Notebook settings > Hardware Accelerator > Select "GPU".

### 1. Clone the code to Colab and install requirements
(The ERROR / WARNING messages during `pip install` are caused by Colab pre-installed packages and can be ignored.)

In [22]:
!git clone https://github.com/QianliM/CAPE.git
%cd CAPE/
!pip uninstall -y tensorflow # uninstall the pre-installed TF2.X in Colab
!pip install -r requirements.txt

Cloning into 'CAPE'...
remote: Enumerating objects: 153, done.
remote: Counting objects: 100% (153/153), done.
remote: Compressing objects: 100% (114/114), done.
remote: Total 153 (delta 75), reused 111 (delta 36), pack-reused 0
Receiving objects: 100% (153/153), 9.15 MiB | 12.05 MiB/s, done.
Resolving deltas: 100% (75/75), done.
/CAPE


### 2. Download the pre-trained model

In [23]:
!mkdir -p checkpoints
%cd checkpoints/
!gdown "https://drive.google.com/uc?id=1UN6zCXul7wDIaYWc86qF5YxAl9eOVCrI"
!unzip CAPE-affineconv_nz64_pose32_clotype32_male.zip
!rm CAPE-affineconv_nz64_pose32_clotype32_male.zip

/CAPE/checkpoints
Downloading...
From: https://drive.google.com/uc?id=1UN6zCXul7wDIaYWc86qF5YxAl9eOVCrI
To: /CAPE/checkpoints/CAPE-affineconv_nz64_pose32_clotype32_male.zip
124MB [00:00, 186MB/s]
Archive:  CAPE-affineconv_nz64_pose32_clotype32_male.zip
  inflating: CAPE-affineconv_nz64_pose32_clotype32_male/checkpoint  
  inflating: CAPE-affineconv_nz64_pose32_clotype32_male/model-115980.index  
  inflating: CAPE-affineconv_nz64_pose32_clotype32_male/model-115980.meta  
  inflating: CAPE-affineconv_nz64_pose32_clotype32_male/model-115980.data-00000-of-00001  


### 3. Run the demo code 
- This will generate a few examples of clothed humans and save to the `results/` folder on the Colab server.
- By setting the `--seed` flag (for random seeds) to other values, you can get different clothing geometry generated.

In [33]:
%cd ..
!python CAPE/run_simple_demo.py --config CAPE/configs/CAPE-affineconv_nz64_pose32_clotype32_male.yaml --seed 12345

/
/usr/local/lib/python3.7/dist-packages/tensorflow/python/framework/dtypes.py:526: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/usr/local/lib/python3.7/dist-packages/tensorflow/python/framework/dtypes.py:527: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/usr/local/lib/python3.7/dist-packages/tensorflow/python/framework/dtypes.py:528: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/usr/local/lib/python3.7/dist-packages/tensorflow/python/framework/dtypes.py:529: FutureWarning: Passing (type, 1) o

### 4. Load the generated examples for visualization

In [71]:
import os
import glob
import numpy as np
import trimesh

objs = glob.glob(os.path.join('CAPE/results', 'demo_results', '*_0000.obj'))
demo_meshes = {}
demo_meshes['minimal'] = trimesh.load(os.path.join('CAPE/data', 'template_mesh.obj'), process=False)
color = np.array((225,225,225, 255)).astype(np.uint8)

for fn in objs:
    clotype = os.path.basename(fn).split('_')[0]

    demo_meshes[clotype] = trimesh.load(fn, process=False)
    normals = demo_meshes[clotype].vertex_normals
    color = ((normals+1)*0.5*255).astype(np.uint8)
    color = np.concatenate((color, np.ones((color.shape[0], 1),dtype=np.uint8)*255), axis=1)
    demo_meshes[clotype].visual.vertex_colors = color

### 5. Run the following 5 cells to visualize in 3D the original undressed body and the generated example of 4 clothing types
- The visualization can be zoomed and rotated.
- As they are generated with the same clothing shape latent variable $z$, they have similar shape style.

In [72]:
# initial minimally-clothed SMPL body
demo_meshes['minimal'].show()

In [73]:
# Clothing type 1: short T-shirt, long pants
demo_meshes['shortlong'].show()

In [74]:
# Clothing type 2: short T-shirt + shorts
demo_meshes['shortshort'].show()

In [75]:
# Clothing type 3: long jersey + shorts
demo_meshes['longshort'].show()

In [70]:
# Clothing type 4: long jersey + long pants
demo_meshes['longlong'].show()

### 6. That's it! You can re-run step 3 providing different random seeds to generate clothing of different shapes.
For the full demo, please visit our [Github repository](https://github.com/QianliM/CAPE).